In [52]:
import numpy as np

p_dist = [0.1, 0.2, 0.3, 0.4]
alphabet = ['a', 'b', 'c', 'd']

info_content = lambda p: np.log2(1/p)
entropy = lambda p_dist: np.sum([p*np.log2(1/p) for p in p_dist])


In [3]:
info_content(p_dist[0])

3.321928094887362

In [4]:
entropy(p_dist)

1.8464393446710154

In [93]:
class TreeNode:
    def __init__(self, data, prob, letter=None):
        self.data = data
        self.prob = prob
        self.letter = letter
        self.leftChild = None
        self.rightChild = None
        self.depth = 0
        self.leaf = True

In [8]:
def lhs_1_rhs_0(node, max_level, level=0):
    if node.rightChild is None:
        node.data = 1
        print('did somthing RHS')
    else:
        print('going lower', level)
        lhs_1_rhs_0(node.rightChild, 3, level+1)
        lhs_1_rhs_0(node.leftChild, 3, level+1)
        return 
            

In [174]:
# TODO: build a class with encode and decode methods for the huffman tree
# TODO: try out the ipython UI plugins to make the tree interactive and visualise it

# Implement Huffmans algorithm to find optimal symbol code given an ensemble X w.p P

class HuffmanAlgo:
    
    def __init__(self, alphabet, P):
        self.alphabet = alphabet
        self.P = P
        self.root = None
        self.tree_depth = 0
        self.encoder = {}
        self.treeString = ''

        
    def create_tree(self):
        # create tree from the leaves, starting with the lowest prob combo
        P_alphabet_join = np.concatenate((np.array(self.P).reshape(len(self.P), 1), \
                                          np.array(self.alphabet).reshape(len(self.alphabet), 1)), axis=1)
        P_sorted = np.sort(P_alphabet_join, axis=0)
#         P_sorted = np.sort(self.P)
        P_sorted = [TreeNode(0, prob, letter) for (prob, letter) in P_alphabet_join]

#         P_sorted = [TreeNode(0, prob) for prob in P_sorted]
        leaf_node = P_sorted[0]
        while len(P_sorted) > 1:
            p_0, p_1 = P_sorted[0].prob, P_sorted[1].prob
            p_0_1 = str(round(float(p_0) + float(p_1),5))
            p_0_1_node = TreeNode(0, p_0_1)
            p_0_1_node.leftChild = P_sorted[0]
            p_0_1_node.rightChild = P_sorted[1]
            p_0_1_node.rightChild.data = 1
            p_0_1_node.leaf = False

#             latest_treeString = p_0_1_node.print_leaves()
#             print(latest_treeString, 'with root prob', p_0_1)

            P_sorted = P_sorted[2:]

            # need to get sorted list of nodes by prob
            P_sorted_plus_new_node = np.concatenate((P_sorted, [p_0_1_node]), axis=0)
            P_sorted = self._sort_nodes_by_prob(P_sorted_plus_new_node)

        self.root = p_0_1_node
        print(self._print_tree(self.root))
                    
        
        return 'Tree Created Of Depth: {}'.format(self.tree_depth)
    
    def _print_tree(self, node, level=0):
        node.depth = level
        if node.depth > self.tree_depth: self.tree_depth = node.depth

        self.treeString = 'letter: '+str(node.letter)+'--- prob:' +str(node.prob) + '--- data:' +str(node.data) +'--- depth:' + str(node.depth) + \
        '--- leaf: '+str(node.leaf) +'--->\n'
        if node.rightChild:
            self.treeString += self._print_tree(node.rightChild, level+1)
        if node.leftChild:
            self.treeString += self._print_tree(node.leftChild, level+1)
        return self.treeString
    
    def _sort_nodes_by_prob(self, node_list):
        idx_prob_lookup = {}
        prob_arr = []
        for idx, node in enumerate(node_list):
            idx_prob_lookup[node.prob] = idx
            prob_arr.append(node.prob)
        prob_arr = np.sort(prob_arr)

        sorted_nodes = []
        for prob in prob_arr:
            idx = idx_prob_lookup[prob]
            sorted_nodes.append(node_list[idx])
        return np.array(sorted_nodes)

    
    def print_tree(self):      
        latest_treeString = self.root.print_leaves()
        return latest_treeString
    
        
    def _get_path_encodings(self, start_node, path_encoding):
        node = start_node
        while node.leaf is False:
            print('adding to:', path_encoding)

            path_encoding+=str(node.data)
            print(path_encoding, '--- PATH')
            if node.rightChild:
                self._get_path_encodings(node.rightChild, path_encoding)
            if node.leftChild:
                self._get_path_encodings(node.leftChild, path_encoding)
        print('LETTER IS ---',node.letter, node.leaf, node.prob)
        if node.leaf is True:
            print(node.leaf, node.prob, node.letter)
            self.encoder[node.letter] = path_encoding
            print(self.encoder)
            return 'reached a leaf node'
                
    def create_encoder(self):
        
        self._get_path_encodings(self.root, '')
        # get all paths to target leaves of tree and append data to encoded_X_dict
        return 'Completed encoder'

    
        
            

In [175]:
algoInst = HuffmanAlgo(P=p_dist, alphabet=alphabet)
print(algoInst.create_tree())

letter: None--- prob:1.0--- data:0--- depth:0--- leaf: False--->
letter: None--- prob:0.6--- data:1--- depth:1--- leaf: False--->
letter: None--- prob:0.3--- data:1--- depth:2--- leaf: False--->
letter: b--- prob:0.2--- data:1--- depth:3--- leaf: True--->
letter: a--- prob:0.1--- data:0--- depth:3--- leaf: True--->
letter: None--- prob:0.3--- data:1--- depth:2--- leaf: False--->
letter: b--- prob:0.2--- data:1--- depth:3--- leaf: True--->
letter: a--- prob:0.1--- data:0--- depth:3--- leaf: True--->
letter: d--- prob:0.4--- data:0--- depth:1--- leaf: True--->

Tree Created Of Depth: 3


In [176]:
algoInst.create_encoder()

adding to: 
0 --- PATH
adding to: 0
01 --- PATH
adding to: 01
011 --- PATH
LETTER IS --- b True 0.2
True 0.2 b
{'b': '011'}
LETTER IS --- a True 0.1
True 0.1 a
{'b': '011', 'a': '011'}
adding to: 011
0111 --- PATH
LETTER IS --- b True 0.2
True 0.2 b
{'b': '0111', 'a': '011'}
LETTER IS --- a True 0.1
True 0.1 a
{'b': '0111', 'a': '0111'}
adding to: 0111
01111 --- PATH
LETTER IS --- b True 0.2
True 0.2 b
{'b': '01111', 'a': '0111'}
LETTER IS --- a True 0.1
True 0.1 a
{'b': '01111', 'a': '01111'}
adding to: 01111
011111 --- PATH
LETTER IS --- b True 0.2
True 0.2 b
{'b': '011111', 'a': '01111'}
LETTER IS --- a True 0.1
True 0.1 a
{'b': '011111', 'a': '011111'}
adding to: 011111
0111111 --- PATH
LETTER IS --- b True 0.2
True 0.2 b
{'b': '0111111', 'a': '011111'}
LETTER IS --- a True 0.1
True 0.1 a
{'b': '0111111', 'a': '0111111'}
adding to: 0111111
01111111 --- PATH
LETTER IS --- b True 0.2
True 0.2 b
{'b': '01111111', 'a': '0111111'}
LETTER IS --- a True 0.1
True 0.1 a
{'b': '01111111', 'a

True 0.2 b
{'b': '01111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111', 'a': '0111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111'}
LETTER IS --- a True 0.1
True 0.1 a
{'b': '01111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111', 'a': '01111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111'}
adding to: 01111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111
011111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111 --- PATH
LETTER IS --- b True 0.2
True 0.2 b
{'b': '0111111111111111111111111111111111111111111111111111111111111111111111111111111111

True 0.2 b
{'b': '01111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111', 'a': '0111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111'}
LETTER IS --- a True 0.1
True 0.1 a
{'b': '01111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111', 'a': '0111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111

LETTER IS --- b True 0.2
True 0.2 b
{'b': '01111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111', 'a': '0111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111'}
LETTER IS --- a True 0.1
True 0.1 a
{'b': '01111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111

True 0.2 b
{'b': '0111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111', 'a': '011111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111

{'b': '011111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111', 'a': '011111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111

LETTER IS --- b True 0.2
True 0.2 b
{'b': '011111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111', 'a': '011111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




LETTER IS --- b True 0.2
True 0.2 b
{'b': '01111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111111

KeyboardInterrupt: 

In [11]:
# Assume alphabet is a, b, c, d and prob dist = p_dist defined above
test_X = 'aabcddd'



In [12]:
import ipywidgets as widgets
from IPython.display import display, clear_output


slider = widgets.IntSlider(
    min=0,
    max=10,
    step=1,
    description='Slider:',
    value=3
)

display(slider)

IntSlider(value=3, description='Slider:', max=10)

In [13]:
slider.value

3

In [14]:
print(dir(widgets))

['Accordion', 'BoundedFloatText', 'BoundedIntText', 'Box', 'Button', 'ButtonStyle', 'CallbackDispatcher', 'Checkbox', 'Color', 'ColorPicker', 'Controller', 'CoreWidget', 'DOMWidget', 'DatePicker', 'Datetime', 'Dropdown', 'FloatLogSlider', 'FloatProgress', 'FloatRangeSlider', 'FloatSlider', 'FloatText', 'HBox', 'HTML', 'HTMLMath', 'Image', 'IntProgress', 'IntRangeSlider', 'IntSlider', 'IntText', 'Label', 'Layout', 'NumberFormat', 'Output', 'Password', 'Play', 'RadioButtons', 'Select', 'SelectMultiple', 'SelectionRangeSlider', 'SelectionSlider', 'SliderStyle', 'Style', 'Tab', 'Text', 'Textarea', 'ToggleButton', 'ToggleButtons', 'ToggleButtonsStyle', 'VBox', 'Valid', 'ValueWidget', 'Widget', '__builtins__', '__cached__', '__doc__', '__file__', '__jupyter_widgets_base_version__', '__jupyter_widgets_controls_version__', '__loader__', '__name__', '__package__', '__path__', '__protocol_version__', '__spec__', '__version__', '_handle_ipython', '_version', 'dlink', 'docutils', 'domwidget', 'fix

In [19]:
# change p_dist and number of variables and create a tree 
# encode and decode any string with a given encoder


create_float_widget = lambda x: widgets.FloatSlider(
    value=1,
    min=0,
    max=1.0,
    step=0.1,
    description='{}:'.format(x),
    disabled=False
)

dimensions_widget = widgets.IntText()
print('Size of alphabet to be coded:')
display(dimensions_widget)

out = widgets.Output()
display(out)
widget_list = []

# Handle changes to the dimension size to prob distribution inputs

def prob_eventhandler(obj):
    global widget_list
    widget_list = [create_float_widget('p{}'.format(i)) for i in range(dimensions_widget.value)]
    with out:
        clear_output()
        print('Probability distribution of alphabet:')
        display(*widget_list)


dimensions_widget.observe(prob_eventhandler, names='value')



Size of alphabet to be coded:


IntText(value=0)

Output()

In [16]:
btn = widgets.Button(description='Create Tree')
display(btn)

out_tree = widgets.Output()
display(out_tree)

def btn_eventhandler(obj):
    p_dist_var = [w.value for w in widget_list]
    algoInst = HuffmanAlgo(p_dist_var)
    with out_tree:
        clear_output()
        print('Prob dist: \n',algoInst.P)
        print(algoInst.create_tree())
btn.on_click(btn_eventhandler)

Button(description='Create Tree', style=ButtonStyle())

Output()

In [17]:
# Implement arithmetic coding

In [18]:
help(np.sort)

Help on function sort in module numpy.core.fromnumeric:

sort(a, axis=-1, kind='quicksort', order=None)
    Return a sorted copy of an array.
    
    Parameters
    ----------
    a : array_like
        Array to be sorted.
    axis : int or None, optional
        Axis along which to sort. If None, the array is flattened before
        sorting. The default is -1, which sorts along the last axis.
    kind : {'quicksort', 'mergesort', 'heapsort'}, optional
        Sorting algorithm. Default is 'quicksort'.
    order : str or list of str, optional
        When `a` is an array with fields defined, this argument specifies
        which fields to compare first, second, etc.  A single field can
        be specified as a string, and not all fields need be specified,
        but unspecified fields will still be used, in the order in which
        they come up in the dtype, to break ties.
    
    Returns
    -------
    sorted_array : ndarray
        Array of the same type and shape as `a`.
   